In [1]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
from fuzzywuzzy import fuzz
from fuzzywuzzy import process
from collections import Counter
import itertools

C:\Users\mansj\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [116]:
# co_auth_df = pd.read_excel("salt_cont_auth.xlsx")
co_auth_df = pd.read_excel("salt_cont_auth_updated_id.xlsx")

Combining the first and last name of the authors

In [117]:
co_auth_df['author_name'] = co_auth_df['author_given_name'] + " " + co_auth_df['author_surname']

#### Checking if there are any null values for the author names

In [118]:
co_auth_df[co_auth_df['author_name'].isna() & co_auth_df['author_given_name'].isna()].index.tolist()
co_auth_df.drop([534], inplace=True)

In [119]:
author_name_list = co_auth_df['author_name'].to_list()
author_name_list[:10]

['Lee Hooper',
 'Christopher Bartlett',
 'George Davey Smith',
 'Shah Ebrahim',
 'L. Hooper',
 'C. Bartlett',
 'G. Davey Smith',
 'S. Ebrahim',
 'Lee Hooper',
 'Christopher Bartlett']

###### Use of fuzzywuzzy to set a threshold and find the acronyms, shortforms for the author names

In [91]:
# score_sort1 = [(x,) + i
#              for x in author_name_list
#              for i in process.extract(x, author_name_list, scorer=fuzz.token_set_ratio)
#               ]
# score_sort1

In [92]:
# df = pd.DataFrame(score_sort1, columns= ["Original name", "Matching Name", "Ratio"])
# df.to_excel("sat_author_name_excel.xlsx", index=False)

In [120]:
# Change the datatype of ID to int for forming a list of co_authors for the id
co_auth_df.ID = co_auth_df.ID.astype("int64")
co_auth_list_df = co_auth_df.groupby(['ID','original_title'])['author_name'].apply(list).reset_index()
co_auth_list_df

ID                                     original_title  \
0    1  Systematic review of long term effects of advi...   
1    2  Reduced dietary salt for prevention of cardiov...   
2    3  Advice to reduce dietary salt for prevention o...   
3    4  Salt intake, stroke, and cardiovascular diseas...   
4    5  Reduced dietary salt for the prevention of car...   
..  ..                                                ...   
76  89  Sodium excretion and risk of developing corona...   
77  90  Association between urinary sodium, creatinine...   
78  91  Urinary sodium and potassium excretion, mortal...   
79  92  Estimated urinary sodium excretion and risk of...   
80  93  Assessing the Associations of Sodium Intake Wi...   

                                          author_name  
0   [Lee Hooper, Christopher Bartlett, George Dave...  
1   [L. Hooper, C. Bartlett, G. Davey Smith, S. Eb...  
2   [Lee Hooper, Christopher Bartlett, George Dave...  
3   [Pasquale Strazzullo, Lanfranco D'Elia, Ngiang...  
4   [Rod S. Taylor, Kate E. Ashton, Tiffany Moxham...  
..                                                ...  
76  [Michel M. Joosten, Ron T. Gansevoort, Kenneth...  
77  [Emily P. McQuarrie, Jamie P. Traynor, Alison ...  
78  [Martin O'Donnell, Andrew Mente, Sumathy Ranga...  
79  [Roman Pfister, Guido Michels, Stephen J. Shar...  
80    [Pamela Singer, Hillel Cohen, Michael Alderman]  

[81 rows x 3 columns]

In [101]:
# co_auth_df[co_auth_df.author_id.isna()]
co_auth_df[co_auth_df.author_surname == "Aburto"]

ID                                     original_title author_given_name  \
25    9  Effect of lower sodium intake on health: syste...          Nancy J.   
529   8  Effect of reduced sodium intake on cardiovascu...                 N   

    author_surname     author_id organizational_author  manual  \
25          Aburto  8.739842e+09                   NaN   False   
529         Aburto  8.739842e+09                   NaN    True   

         author_name  
25   Nancy J. Aburto  
529         N Aburto

In [121]:
co_auth_df_copy = co_auth_df[['author_name','author_id']]
co_auth_df_copy = co_auth_df_copy[~co_auth_df_copy.author_id.isna()]

dup_auth = pd.merge(co_auth_df_copy, co_auth_df_copy, how = "left" , left_on="author_id", right_on="author_id")
dup_auth
dup_auth["dup_name"] = dup_auth[["author_name_x","author_name_y"]].values.tolist()

author_acry_list = [tuple(sorted(list(row))) for row in dup_auth.dup_name if row[0] != row[1]]

author_acry_dict = dict()

for i in set(author_acry_list):
    author_acry_dict[i[0]] = i[1]
    
# print(author_acry_dict)


{'Appel Lawrence': 'Lawrence J. Appel',
 'S. Ebrahim': 'Shah Ebrahim',
 'Hillel Cohen': 'Hillel W. Cohen',
 'Gerjan J. Navis': 'Gerjan Navis',
 'RS Taylor': 'Rod S. Taylor',
 "Martin J. O'Donnell": "Martin O'Donnell",
 'Matthew J. McQueen': 'Matthew McQueen',
 'L. Hooper': 'Lee Hooper',
 'Michael Alderman': 'Michael H. Alderman',
 'G. Davey Smith': 'George Davey Smith',
 'Shiriki K. Kumanyika': 'Shiriki Kumanyika',
 'Johan Wad??en': 'Johan Wad??n',
 'ML Chung': 'Misook L. Chung',
 'DK Moser': 'Debra K. Moser',
 'John H. Laragh': 'John Laragh',
 'J Cohen': 'JD Cohen',
 'C. Bartlett': 'Christopher Bartlett',
 'Jean E. Sealey': 'Jean Sealey',
 'N Aburto': 'Nancy J. Aburto',
 'TA Lennie': 'Terry A. Lennie',
 'John L. Moran': 'John Moran'}

In [104]:
#old version of fuzzy word matching

# dup_df = pd.read_csv("duplicate_name.csv")

# dup_dict = pd.Series(dup_df.Dup.values, index = dup_df.Og).to_dict()
# dup_dict

In [122]:
def replace_auth_name(author_list, author_acry_dict):
    for i in range(len(author_list)):
        for k, v in author_acry_dict.items():
            if author_list[i] in v:
                author_list[i] = author_list[i].replace(author_list[i], k)
                
    return author_list

In [123]:
co_auth_list_df.author_name = co_auth_list_df.author_name.apply(lambda x: replace_auth_name(x, dup_dict))
# co_auth_list_df.head()

ID                                     original_title  \
0   1  Systematic review of long term effects of advi...   
1   2  Reduced dietary salt for prevention of cardiov...   
2   3  Advice to reduce dietary salt for prevention o...   
3   4  Salt intake, stroke, and cardiovascular diseas...   
4   5  Reduced dietary salt for the prevention of car...   

                                         author_name  
0  [L. Hooper, C. Bartlett, G. Davey Smith, S. Eb...  
1  [L. Hooper, C. Bartlett, G. Davey Smith, S. Eb...  
2  [L. Hooper, C. Bartlett, G. Davey Smith, S. Eb...  
3  [Pasquale Strazzullo, Lanfranco D'Elia, Ngiang...  
4  [RS Taylor, Kate E. Ashton, Tiffany Moxham, L....

In [124]:
un_auth_names = list(set([a.strip() for b in co_auth_list_df.author_name.tolist() for a in b]))
un_auth_names[:10]

['Yutaka Inaba',
 'Robert Luben',
 'Ping Da Bian',
 'Elif I. Ekinci',
 'Yanling Zhang',
 'Yasuhiro Hasegawa',
 'M. A. Hern??n',
 'Taichi Shimazu',
 'Jianhua Qi',
 'Jeanne Charleston']

In [125]:
edge_list = co_auth_list_df['author_name'].values.tolist()
len(edge_list)

81

Total number of papers are 81 and to find the combinations for the code to run in an efficient way do the below

In [126]:
new = []
for i in edge_list:
    if len(i) >=2:
        for subset in itertools.combinations(i,2):
            if len(subset) == 2:
                new.append(subset)

In [21]:
sorted_list = []
# individual_authors = []
for i in new:
    sorted_list.append(tuple(sorted(list(i))))
#     for j in i:
#         individual_authors.append(j)

In [112]:
count_auth = Counter(sorted_list)
# updated_auth_nodes = []

# indi_auth_count = Counter(individual_authors)
# for k, v in sorted(indi_auth_count.items(), key = lambda x : x[1], reverse=True):
#     if v >= 20:
#         updated_auth_nodes.append(k)

# len(updated_auth_nodes)

In [113]:
sorted(count_auth.items(), key = lambda x : x[1], reverse=True)

[(('Hillel Cohen', 'Michael Alderman'), 6),
 (('P DiPasquale', 'Salvatore Paterna'), 6),
 (('L. Hooper', 'S. Ebrahim'), 5),
 (('Appel Lawrence', 'Paul K. Whelton'), 5),
 (('Gaspare Parrinello', 'P DiPasquale'), 5),
 (('Gaspare Parrinello', 'Salvatore Paterna'), 5),
 (('Salvatore Paterna', 'Sergio Fasullo'), 5),
 (('P DiPasquale', 'Sergio Fasullo'), 5),
 (('Filippo M. Sarullo', 'Salvatore Paterna'), 4),
 (('Filippo M. Sarullo', 'P DiPasquale'), 4),
 (('Gaspare Parrinello', 'Sergio Fasullo'), 4),
 (('Filippo M. Sarullo', 'Sergio Fasullo'), 4),
 (('C. Bartlett', 'L. Hooper'), 3),
 (('G. Davey Smith', 'L. Hooper'), 3),
 (('C. Bartlett', 'G. Davey Smith'), 3),
 (('C. Bartlett', 'S. Ebrahim'), 3),
 (('G. Davey Smith', 'S. Ebrahim'), 3),
 (('Kate E. Ashton', 'S. Ebrahim'), 3),
 (('Michael Alderman', 'Shantha Madhavan'), 3),
 (('Hillel Cohen', 'Shantha Madhavan'), 3),
 (('Paul K. Whelton', 'Shiriki Kumanyika'), 3),
 (('Jeffrey A. Cutler', 'Paul K. Whelton'), 3),
 (('Appel Lawrence', 'Shiriki K

In [114]:
node_names = un_auth_names
G = nx.Graph()
G.add_nodes_from(node_names)

for k, v in count_auth.items():
    if k[0] in G.nodes() or k[1] in G.nodes():
        G.add_edge(k[0],k[1], weight = v,  length = v)
        

d = nx.degree_centrality(G)

sorted(d.items(), key = lambda x : x[1], reverse = True)

[('Yanling Zhang', 0.08333333333333334),
 ('Jianhua Qi', 0.08333333333333334),
 ('Carlene Lawes', 0.08333333333333334),
 ("John Fa'atui", 0.08333333333333334),
 ('Rachel Huxley', 0.08333333333333334),
 ('Jingpu Shi', 0.08333333333333334),
 ('Anthony Rodgers', 0.08333333333333334),
 ('Junxiang Liu', 0.08333333333333334),
 ('Andrew Mente', 0.08333333333333334),
 ('Salim Yusuf', 0.08333333333333334),
 ('Jianmin Li', 0.08333333333333334),
 ('Dongshuang Guo', 0.08333333333333334),
 ('Donglin Song', 0.08333333333333334),
 ('Koon Teo', 0.08333333333333334),
 ('Bailing Chen', 0.08333333333333334),
 ("Martin O'Donnell", 0.08333333333333334),
 ('Colleen Ng', 0.08333333333333334),
 ('Michelle Barlow', 0.08333333333333334),
 ('Yuming Li', 0.08333333333333334),
 ('Rujun Pan', 0.08333333333333334),
 ('Simon Pink', 0.08333333333333334),
 ('Yongqing Yang', 0.08333333333333334),
 ('Nicole Li', 0.08333333333333334),
 ('Yangfeng Wu', 0.08333333333333334),
 ('Suzanne Ryan', 0.08333333333333334),
 ('Beifan

In [115]:
plt.figure(figsize=(300, 300))

# pos = nx.spring_layout(G)
# pos = nx.nx_agraph.graphviz_layout(G)
edges = G.edges()
weights = [G[u][v]['weight'] for u,v in edges]
nx.draw(G, font_size = 30, nodelist=dict(d).keys(), node_size=[v * 10000 for v in dict(d).values()], with_labels = True, 
        width = weights)
plt.savefig('auth.jpg')

In [18]:
from netwulf import visualize
styled_network, config = visualize(G)
plt.savefig('auth1.jpg')

<Figure size 432x288 with 0 Axes>